In [1]:
import os
import cv2
import pycolmap
from hloc.utils import viz_3d
import numpy as np
import pixtrack.utils.pose_utils as pose_utils
from pixloc.utils.colmap import Camera as ColCamera
from pixloc.pixlib.geometry import Camera as PixCamera, Pose
import matplotlib.pyplot as plt
from pixtrack.utils.ingp_utils import load_nerf2sfm, initialize_ingp, sfm_to_nerf_pose, nerf_to_sfm_pose
from pixtrack.visualization.run_vis_on_poses import get_nerf_image
from scipy.spatial.transform import Rotation as R

In [2]:
sfm_path = '/home/wayve/data/pixtrack/outputs/nerf_sfm/gimble_mar12_2023/sfm/'
model = pycolmap.Reconstruction(sfm_path)


nerf_path = '/home/wayve/data/pixtrack/instant-ngp/snapshots/gimble_mar12_2023/weights.msgpack'
nerf2sfm_path = '/home/wayve/data/pixtrack/pixel-perfect-sfm/datasets/gimble_mar12_2023/nerf2sfm.pkl'
nerf2sfm = load_nerf2sfm(nerf2sfm_path)
aabb_with_table = [[0.090, -0.493, -0.113], [0.895, 0.065, 0.714]] # this is for the gimbal
testbed = initialize_ingp(nerf_path, background=np.array([0, 0, 0, 0.0]), aabb=[[0.302, -0.386, 0.209], [0.735, 0.108, 0.554]])#, aabb=aabb_with_table)

04:59:21 INFO     Loading network config from: /home/wayve/data/pixtrack/instant-ngp/snapshots/gimble_mar12_2023/weights.msgpack
04:59:21 INFO     GridEncoding:  Nmin=16 b=1.51572 F=2 T=2^19 L=16
04:59:21 INFO     Density model: 3--[HashGrid]-->32--[FullyFusedMLP(neurons=64,layers=3)]-->1
04:59:21 INFO     Color model:   3--[Composite]-->16+16--[FullyFusedMLP(neurons=64,layers=4)]-->3
04:59:21 INFO       total_encoding_params=13074912 total_network_params=10240


In [3]:
camera = model.cameras[1]
camera = ColCamera(None, 
                camera.model_name,
                int(camera.width),
                int(camera.height),
                camera.params)
camera = PixCamera.from_colmap(camera)

In [4]:
!pip3 install mediapy

In [5]:
from scipy.spatial.transform import Rotation as R
from scipy.spatial.transform import Slerp

In [6]:
import mediapy

In [7]:
!mkdir /data/pixtrack/outputs/gimbal_assets

mkdir: cannot create directory ‘/data/pixtrack/outputs/gimbal_assets’: No such file or directory


In [9]:
from tqdm import tqdm 

In [10]:
elevation = 3
radius = 5.0
up_axis = 1
num_views = 720
render_poses = np.stack(
        [
            pose_spherical(angle, elevation, radius, up_axis - 1)
            for angle in np.linspace(-180, 180, num_views + 1)[:-1]
        ],
        0,
    )  # (NV, 4, 4)

for i in range(render_poses.shape[0]):
    render_poses[i, :3, 3] -= [0.0, 0., 2.0]    

image_renders = []
second_renders = []
testbed.background_color = [255, 255, 255, 255]
#testbed.nerf.rendering_min_transmittance = 0.8
#testbed.rendering_min_alpha = 1e-4 * 10
#testbed.exposure = 0.1
for image_num, camera_pose in enumerate(tqdm(render_poses)):
    nerf_img = get_nerf_image(testbed, camera_pose, camera)
    image_renders.append(nerf_img.copy())

    #Image.fromarray(nerf_img).save(os.path.join(render_output_path, f"{image_num}.jpg"))
    #gray = cv2.cvtColor(nerf_img, cv2.COLOR_RGB2GRAY) # convert to grayscale
    #blur = cv2.blur(gray, (3, 3)) # blur the image
    #ret, thresh = cv2.threshold(np.uint8(255) - blur, 210, 255, cv2.THRESH_BINARY)
    #contours, hierarchy = cv2.findContours(thresh, cv2.RETR_TREE, cv2.CHAIN_APPROX_NONE)
    #img = cv2.fillPoly(nerf_img, pts = contours, color =(0, 255, 75))
    #mask = np.array((img != np.array([0, 255, 75]))*np.array([0, 255, 75]), dtype=np.uint8)

    # Plotting the contours images
    #result_img = cv2.drawContours(nerf_img.copy(), contours, -1, (0,255,75), 2)
    #second_renders.append(result_img)

  0%|                                                                                                                                                                                        | 0/720 [00:00<?, ?it/s]/home/wayve/saurabh/pixtrack/pixtrack/visualization/run_vis_on_poses.py:28: RuntimeWarning: invalid value encountered in cast
  nerf_img = nerf_img.astype(np.uint8)
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 720/720 [11:25<00:00,  1.05it/s]


In [11]:
mediapy.show_video(image_renders, width=640, height=480, fps=30)


This browser does not support the video tag.


In [43]:
point_ids = []
points3d_in_nerf = []
one_cam_pose = pose_utils.get_camera_in_world_from_colmap_image(model.images[1])
one_cam_pose_in_nerf = sfm_to_nerf_pose(nerf2sfm=nerf2sfm, sfm_pose=one_cam_pose)
for point_id, point in enumerate(model.points3D):
    point_ids.append(point)
    pose_placeholder = np.eye(4)
    pose_placeholder[:3, -1] = model.points3D[point].xyz
    pose_placeholder_nerf = sfm_to_nerf_pose(nerf2sfm=nerf2sfm, sfm_pose=pose_placeholder)[:3, -1]
    pose_placeholder_nerf, one_cam_pose_in_nerf
    points3d_in_nerf.append(pose_placeholder_nerf)
    
points3d_in_nerf = np.array(points3d_in_nerf)


In [ ]:
from sklearn.cluster import DBSCAN
clustering = DBSCAN(eps=0.1, min_samples=2).fit(points3d_in_nerf)

In [72]:
min_pts = np.min(points3d_in_nerf[clustering.core_sample_indices_], axis=0)

In [73]:
max_pts = np.max(points3d_in_nerf[clustering.core_sample_indices_], axis=0)

In [82]:
max_bounds = max_pts/3 + np.array([0.5, 0.5, 0.5])

array([0.53972258, 0.70492362, 0.1010544 ])

In [90]:
min_bounds = min_pts/3 + np.array([0.5, 0.5, 0.5])

In [92]:
min_bounds = [min_bounds[1], min_bounds[2], min_bounds[0]]

In [93]:
max_bounds = max_pts/3 + np.array([0.5, 0.5, 0.5])

In [94]:
max_bounds = [max_bounds[1], max_bounds[2], max_bounds[0]]

In [96]:
aabb_bounds = [min_bounds, max_bounds]

In [97]:
aabb_bounds

[[0.3126329728260778, -0.4284740002233347, 0.1993532796217375],
 [0.704923619286159, 0.1010543981393473, 0.5397225802093615]]